In [1]:
import IPython.display as ipd
import sys
sys.path.append("/mnt/research/germs/shane/transActRNA/scripts/")
from AnnotateTree import *
from BCBio import GFF
from CRISPRtools import *
from glob import glob
from os import chdir,listdir, system
from pandas import DataFrame, read_excel, read_csv
from pickle import load
done = ipd.Audio('/mnt/research/germs/shane/transActRNA/DoneSound.wav',autoplay=True)
chdir("/mnt/research/germs/shane/hgt/data")

In [14]:
casOperons=load(open("pickles/Cas1_Class2_OperonsReduced.p",'rb'))
done

In [2]:
print("Loading")
# crisprs = load(open("/mnt/research/germs/shane/hgt/data/pickles/RefSeqCRISPRs.p","rb"))
casOperons=load(open("pickles/Cas12_Operons_HMM.p",'rb'))
done

Loading


In [4]:
masterDF=read_csv("tables/MasterDF.csv")
masterDF.set_index("Accession",inplace=True)
masterDF

/mnt/home/dooleys1/bin/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3147: DtypeWarning: Columns (1) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


HasCRISPR?  annoCRISPR?   Cas1   Cas2   Cas9  Cas12  annoCas1  \
Accession                                                                       
GCF_003394085.1      False        False  False  False  False  False     False   
GCF_000740335.1      False        False  False  False  False  False     False   
GCF_006441575.1      False        False  False  False  False  False     False   
GCF_001978415.1      False        False  False  False  False  False     False   
GCF_001588735.1       True         True   True  False   True  False      True   
...                    ...          ...    ...    ...    ...    ...       ...   
GCF_013738135.1       True        False  False  False  False  False     False   
GCF_009872775.1      False        False  False  False  False  False     False   
GCF_000562285.1       True        False  False  False  False  False     False   
GCF_001215565.1       True        False  False  False  False  False     False   
GCF_013307165.1        NaN         True  False  False  False  False     False   

                 annoCas2  annoCas9  annoCas12  ...  ProtID  Cas12Rep?  Perc  \
Accession                                       ...                            
GCF_003394085.1     False     False      False  ...     NaN      False   NaN   
GCF_000740335.1     False     False      False  ...     NaN      False   NaN   
GCF_006441575.1     False     False      False  ...     NaN      False   NaN   
GCF_001978415.1     False     False      False  ...     NaN      False   NaN   
GCF_001588735.1      True      True      False  ...     NaN      False   0.0   
...                   ...       ...        ...  ...     ...        ...   ...   
GCF_013738135.1     False     False      False  ...     NaN      False   NaN   
GCF_009872775.1     False     False      False  ...     NaN      False   NaN   
GCF_000562285.1     False     False      False  ...     NaN      False   NaN   
GCF_001215565.1     False     False      False  ...     NaN      False   NaN   
GCF_013307165.1     False     False      False  ...     NaN      False   NaN   

                               Cas1ProtID  Cas9ProtID  Cas1Rep?  Cas2ProtID  \
Accession                                                                     
GCF_003394085.1                       NaN         NaN       NaN         NaN   
GCF_000740335.1                       NaN         NaN       NaN         NaN   
GCF_006441575.1                       NaN         NaN       NaN         NaN   
GCF_001978415.1                       NaN         NaN       NaN         NaN   
GCF_001588735.1  NZ_LAVY01000011.1_ORF270         NaN       NaN         NaN   
...                                   ...         ...       ...         ...   
GCF_013738135.1                       NaN         NaN       NaN         NaN   
GCF_009872775.1                       NaN         NaN       NaN         NaN   
GCF_000562285.1                       NaN         NaN       NaN         NaN   
GCF_001215565.1                       NaN         NaN       NaN         NaN   
GCF_013307165.1                       NaN         NaN       NaN         NaN   

                 Cas2Rep?  Cas9Rep? Cas12ProtID  
Accession                                        
GCF_003394085.1     False     False         NaN  
GCF_000740335.1     False     False         NaN  
GCF_006441575.1     False     False         NaN  
GCF_001978415.1     False     False         NaN  
GCF_001588735.1     False     False         NaN  
...                   ...       ...         ...  
GCF_013738135.1     False     False         NaN  
GCF_009872775.1     False     False         NaN  
GCF_000562285.1     False     False         NaN  
GCF_001215565.1     False     False         NaN  
GCF_013307165.1     False     False         NaN  

[203474 rows x 29 columns]

In [10]:
refSeqPath="/mnt/research/germs/shane/databases/assemblies/NCBI/refseq/bacteria"
gffFiles = set(glob("%s/*.gff" % (refSeqPath)))
interestTypes = set(["CDS",'gene'])
c=0
bad,good = set(),set()
for accession, operon in casOperons:
    if path.exists("/mnt/research/germs/shane/hgt/data/proteins/16S/cas12/%s.faa" % (accession)):continue
    gff = operon.assembly.replace(".fasta",".gff")
    if not gff in gffFiles:
        bad.add(gff)
        continue
    with open(gff) as fh:
        ascession = gff[gff.rfind("/")+1:-4]
        for rec in GFF.parse(fh):
            for feature in rec.features: 
                try:masterDF.at[ascession,feature.type]+=1
                except: pass
                for subfeature in feature.sub_features:
                    if subfeature.type not in interestTypes:continue
                    if "product" in subfeature.qualifiers and "16S" in subfeature.qualifiers['product'][0]:
                        if "Note" in subfeature.qualifiers and "incomplete" in subfeature.qualifiers['Note'][0]:continue
                        try:
                            if not path.exists("proteins/16S/%s.faa"%(ascession)):
                                system("esearch -db protein -query \"%s\" |efetch -format fasta &>proteins/16S/cas12/%s.faa" %(subfeature.qualifiers['Name'][0],ascession) )
                                sleep(1)
                                c+=1
                            good.add(ascession)
                            masterDF.at[ascession,'16S Present']=True
                            break
                        except: 
                            bad.add(gff)
                            print("Exception:",ascession,subfeature,"\n")
                if accession in good:break
            if accession in good:break
# masterDF.to_csv("tables/HGT_Metadata.csv")
                    
c, len(casOperons),len(bad),len(good)

Exception: GCF_902506115.1 type: CDS
location: [3700081:3701416](-)
id: cds-WP_159147022.1
qualifiers:
    Key: Dbxref, Value: ['Genbank:WP_159147022.1']
    Key: ID, Value: ['cds-WP_159147022.1']
    Key: Name, Value: ['WP_159147022.1']
    Key: Parent, Value: ['gene-GVZ27_RS18320']
    Key: gbkey, Value: ['CDS']
    Key: gene, Value: ['rsmB']
    Key: inference, Value: ['COORDINATES: similar to AA sequence:RefSeq:WP_002160724.1']
    Key: locus_tag, Value: ['GVZ27_RS18320']
    Key: phase, Value: ['0']
    Key: product, Value: ['16S rRNA (cytosine(967)-C(5))-methyltransferase RsmB']
    Key: protein_id, Value: ['WP_159147022.1']
    Key: source, Value: ['Protein Homology']
    Key: transl_table, Value: ['11']
 

Exception: GCF_902506115.1 type: CDS
location: [3759580:3760513](-)
id: cds-WP_002014746.1
qualifiers:
    Key: Dbxref, Value: ['Genbank:WP_002014746.1']
    Key: ID, Value: ['cds-WP_002014746.1']
    Key: Name, Value: ['WP_002014746.1']
    Key: Parent, Value: ['gene-GVZ27_R

AssertionError: >NZ_LN831776.1 Paenibacillus riograndensis SBR5 isolate SBR5(T) chromosome I

In [5]:
def pullCoords(descr):
    startIndex = descr.find("from ")+5
    isComplement = False
    strand = "+"
    if descr[startIndex]=='c':
        startIndex+=11
        isComplement=True
        strand="-"
    endIndex = descr.find("..",startIndex)
    startCoord = int(descr[startIndex:endIndex])
    if isComplement:
        chrIndex = descr.find(") of ",endIndex)
        endCoord = int(descr[endIndex+2:chrIndex])
        buffer=5
    else:
        chrIndex = descr.find(" of ",endIndex)
        endCoord = int(descr[endIndex+2:chrIndex])
        buffer = 4
    endChrIndex = descr.find(" ",chrIndex+buffer)
    if strand=='-': chrName = descr[chrIndex+5:endChrIndex]
    else:chrName = descr[chrIndex+4:endChrIndex]
    return int(startCoord), int(endCoord), strand, chrName

In [4]:
len(casOperons)

39590

In [6]:
from Bio import SearchIO
scratch = "/mnt/gs18/scratch/users/dooleys1/hgt/orfs/%s.orfs"
difCHR, multipleCHRs, dup = 0,0,0
seqNames=set()
proteinSeqs = open("proteins/All_Cas2-Like.faa",'w')
fh = open("assemblies/Cas2Coding.fa",'w')
i=0
for asm,operon in casOperons:
    if len(operon.prots)>1: 
        multipleCHRs += 1
        continue
    assembly = fasta_index(operon.assembly,"fasta")
    protID = list(operon.prots.keys())[0]
    if protID in seqNames:dup+=1;continue
    operon.protID = protID
    hmmResult = SearchIO.read("proteins/searches/cas2/" + asm + ".cas2.hmmout", 'hmmer3-text')
    start, end, strand, chrName = pullCoords(hmmResult.hits[0].description)
    if chrName not in protID:
        difCHR+=1
        continue
    seqNames.add(protID)
    try:rec=assembly[chrName]
    except:
        print(hmmResult.hits[0].description)
        print(pullCoords(hmmResult.hits[0].description))
        break
    rec.description=""
    rec.name=protID
    rec.id=protID
    if strand == '-': rec.seq = rec.seq[start:end].reverse_complement()
    else: rec.seq = rec.seq[start:end]
    write(rec,fh,"fasta")
    write(operon.prots[protID],proteinSeqs,"fasta")
    i+=1
    if i % 5000==0:
        fh.close()
        proteinSeqs.close()
        print(i)
        proteinSeqs = open("proteins/All_Cas2-Like.faa",'a')
        fh = open("assemblies/Cas2Coding.fa",'a')
fh.close()
proteinSeqs.close()
done

5000
10000
15000
20000
25000
30000
35000


In [ ]:
difCHR,multipleCHRs,dup

In [ ]:
#Get the nucleotide sequence for the protein coding region for each protein

casOperons=load(open("pickles/AllCasOps.p",'rb'))

In [123]:
# Update the masterDF with what proteins were found in my pipeline
# masterDF["Cas1"] = False
# masterDF["Cas2"] = False
# masterDF["Cas9"] = False
# masterDF["Cas12"] = False
casOperons=load(open("pickles/AllCasOps.p",'rb'))
print("Ops loaded")
for prot in ["Cas1","Cas2","Cas9","Cas12"]: 
    if prot not in casOperons: casOperons[prot] = load(open("pickles/%s_Operons_HMM.p" % (prot),"rb"))
    if "Cas2" == prot:
        for accession in masterDF.index: masterDF.at[accession,prot] = (accession in casOperons[prot].keys())
    print("Found %i genome assemblies with %s" % (len(masterDF[masterDF[prot]==True]),prot))
print("There are %i genome assemblies with both Cas9 and Cas12" % (len(masterDF[((masterDF["Cas9"]==True)&(masterDF["Cas12"]==True))])))
masterDF.to_csv("tables/MasterDF.csv")
done
# dump(casOperons,open("pickles/AllCasOps.p",'wb'))

Found 71115 genome assemblies with Cas1
Found 13203 genome assemblies with Cas2
Found 28007 genome assemblies with Cas9
Found 6054 genome assemblies with Cas12
There are 1590 genome assemblies with both Cas9 and Cas12


In [109]:
#Update the masterDF with what proteins were already identified by RefSeq
masterDF["annoCas1"] = False
masterDF["annoCas2"] = False
masterDF["annoCas9"] = False
masterDF["annoCas12"] = False
annos=0
interest = set(["Cas1","Cas2","Cas9","Cas12"])
for accession in masterDF.index:
    subDF = df[df["Accession"] == accession]
    if subDF.shape[0] > 0:
        subsub = subDF[subDF["Gene"].isin(interest)]
        for gene in subsub['Gene'].unique(): masterDF.at[accession,"anno"+gene]=True; annos+=1
annos

149100

In [122]:
done

In [111]:
masterDF.to_csv("tables/MasterDF.csv")

In [2]:
masterDF = read_csv("tables/MasterDF.csv")
masterDF.set_index("Accession",inplace=True)
masterDF.head()

/mnt/home/dooleys1/bin/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3146: DtypeWarning: Columns (1) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


HasCRISPR?  annoCRISPR?   Cas1   Cas2   Cas9  Cas12  annoCas1  \
Accession                                                                       
GCF_003394085.1      False        False  False  False  False  False     False   
GCF_000740335.1      False        False  False  False  False  False     False   
GCF_006441575.1      False        False  False  False  False  False     False   
GCF_001978415.1      False        False  False  False  False  False     False   
GCF_001588735.1       True         True   True  False   True  False      True   

                 annoCas2  annoCas9  annoCas12  
Accession                                       
GCF_003394085.1     False     False      False  
GCF_000740335.1     False     False      False  
GCF_006441575.1     False     False      False  
GCF_001978415.1     False     False      False  
GCF_001588735.1      True      True      False

In [5]:
cas9Tree = Tree("trees/old/RAxML_bestTree.Cas9.tre")
len(cas9Tree)

1461

In [12]:
oldCas9 = load(open("/mnt/research/germs/shane/transActRNA/data/pickles/Cas9_Operons.p",'rb'))
done

In [6]:
operons = load(open("pickles/Cas9_Operons_HMM.p",'rb'))
oldCas9 = load(open("/mnt/research/germs/shane/transActRNA/data/pickles/Cas9_Operons.p",'rb'))

In [18]:
c=0
for leaf in cas9Tree.get_leaf_names():
    try:op = operons[leaf]
    except: 
        try:
            op = oldCas9[leaf]
            asm = op.assembly[op.assembly.rfind('/')+1:].replace(".fasta","")
            operons[leaf]=op
        except: c+=1

0

In [20]:
masterDF["Cas9 Name"]=""
for leaf in cas9Tree.get_leaf_names():
    op = operons[leaf]
    asm = op.assembly[op.assembly.rfind('/')+1:].replace(".fasta","")
    masterDF.at[asm,"Cas9 Name"]=leaf    

In [21]:
masterDF[masterDF["Cas9 Name"]!=""]

HasCRISPR? annoCRISPR?   Cas1   Cas2  Cas9  Cas12 annoCas1  \
Accession                                                                    
GCF_902363885.1       True        True   True  False  True  False     True   
GCF_007750855.1       True        True   True   True  True  False     True   
GCF_005281475.1       True        True  False  False  True  False     True   
GCF_009831105.1       True        True   True  False  True  False     True   
GCF_012396585.1       True        True   True  False  True  False     True   
...                    ...         ...    ...    ...   ...    ...      ...   
GCF_003143775.1       True        True   True   True  True  False     True   
GCF_003386095.1       True        True   True   True  True  False     True   
GCF_000768855.1       True        True  False  False  True  False     True   
GCF_001060545.1       True        True  False  False  True  False     True   
GCA_012273615.1        NaN         NaN    NaN    NaN   NaN    NaN      NaN   

                annoCas2 annoCas9 annoCas12                    Cas9 Name  
Accession                                                                 
GCF_902363885.1     True     True     False  NZ_CABJBY010000019.1_ORF229  
GCF_007750855.1     True    False     False      NZ_CP036291.1_ORF100159  
GCF_005281475.1     True     True     False      NZ_CP040106.1_ORF275337  
GCF_009831105.1     True     True     False   NZ_WUUQ01000001.1_ORF38039  
GCF_012396585.1     True     True     False  NZ_JAAXPR010000001.1_ORF699  
...                  ...      ...       ...                          ...  
GCF_003143775.1     True    False     False     NZ_QFRJ01000015.1_ORF792  
GCF_003386095.1     True     True     False    NZ_QREG01000022.1_ORF3207  
GCF_000768855.1     True     True     False    NZ_JRAN01000059.1_ORF2091  
GCF_001060545.1     True    False     False   NZ_JVYQ01000014.1_ORF10489  
GCA_012273615.1      NaN      NaN       NaN          CP050995.1_ORF41019  

[1461 rows x 11 columns]

In [28]:
reps = read_csv("tables/RepresentativeTypeII_Data.csv")
reps.set_index("Accession",inplace=True)
reps.head()

ProtID                        Leaf Name  \
Accession                                                                      
GCF_002797935.1  NZ_PGER01000001.1_ORF25054   999_NZ_PGER01000001_1_ORF25054   
GCF_000614025.1    NZ_BAKF01000012.1_ORF274    1323_NZ_BAKF01000012_1_ORF274   
GCF_003859965.1   NZ_RQYR01000002.1_ORF4433    740_NZ_RQYR01000002_1_ORF4433   
GCF_001373255.1  NZ_CDRJ01000001.1_ORF54257  1222_NZ_CDRJ01000001_1_ORF54257   
GCF_004916905.1   NZ_SDLV01000053.1_ORF4166    622_NZ_SDLV01000053_1_ORF4166   

                 PseudoChromosomes  Genome Size (BP)  Prodigal Genes  \
Accession                                                              
GCF_002797935.1                  1           5351669            8806   
GCF_000614025.1                148           3002170            5944   
GCF_003859965.1                 86           3107355            5818   
GCF_001373255.1                  1           5621065            9980   
GCF_004916905.1                 64           4688351            8554   

                 PhageFinder  ISEScan      Perc    GC Cont  GC Count  \
Accession                                                              
GCF_002797935.1          172        0  0.040414  34.419991   1842044   
GCF_000614025.1          190        0  0.087517  38.917483   1168369   
GCF_003859965.1          109        0  0.038984  66.988548   2081572   
GCF_001373255.1          273        0  0.057888  65.779990   3697536   
GCF_004916905.1          147        0  0.035354  36.019317   1688712   

                 RefSeq Genes  RefSeq Pseudogenes  Representative?  
Accession                                                           
GCF_002797935.1          4256                 104             True  
GCF_000614025.1          2171                 398             True  
GCF_003859965.1          2796                  63             True  
GCF_001373255.1          4716                 421             True  
GCF_004916905.1          4158                  69             True

In [31]:
from pandas import concat
result = concat([cas9DF,reps],axis=1,join='outer')
result.head()

HasCRISPR? annoCRISPR?   Cas1   Cas2  Cas9  Cas12 annoCas1  \
GCF_902363885.1       True        True   True  False  True  False     True   
GCF_007750855.1       True        True   True   True  True  False     True   
GCF_005281475.1       True        True  False  False  True  False     True   
GCF_009831105.1       True        True   True  False  True  False     True   
GCF_012396585.1       True        True   True  False  True  False     True   

                annoCas2 annoCas9 annoCas12  ... Genome Size (BP)  \
GCF_902363885.1     True     True     False  ...        2560730.0   
GCF_007750855.1     True    False     False  ...        6618662.0   
GCF_005281475.1     True     True     False  ...        6064527.0   
GCF_009831105.1     True     True     False  ...        2299421.0   
GCF_012396585.1     True     True     False  ...        2467419.0   

                Prodigal Genes PhageFinder  ISEScan      Perc    GC Cont  \
GCF_902363885.1         5406.0       125.0      0.0  0.058575  44.529490   
GCF_007750855.1        10376.0       204.0      0.0  0.040428  66.449986   
GCF_005281475.1         9852.0       211.0      0.0  0.045182  44.139996   
GCF_009831105.1         4490.0       144.0      0.0  0.063604  42.219759   
GCF_012396585.1         4716.0       119.0      0.0  0.053149  42.748921   

                  GC Count  RefSeq Genes  RefSeq Pseudogenes  Representative?  
GCF_902363885.1  1140280.0        2134.0               337.0             True  
GCF_007750855.1  4398100.0        5046.0               100.0             True  
GCF_005281475.1  2676882.0        4670.0                61.0             True  
GCF_009831105.1   970810.0        2264.0                29.0             True  
GCF_012396585.1  1054795.0        2239.0               118.0             True  

[5 rows x 24 columns]

In [32]:
result.shape

(1462, 24)

In [25]:
cas9DF = masterDF[masterDF["Cas9 Name"]!=""]
from numpy import nan
cas9DF[((cas9DF["HasCRISPR?"]!=True)&(cas9DF["HasCRISPR?"]!=False))]

HasCRISPR? annoCRISPR? Cas1 Cas2 Cas9 Cas12 annoCas1 annoCas2  \
Accession                                                                       
GCA_012273615.1        NaN         NaN  NaN  NaN  NaN   NaN      NaN      NaN   

                annoCas9 annoCas12            Cas9 Name  
Accession                                                
GCA_012273615.1      NaN       NaN  CP050995.1_ORF41019

In [27]:
cas9DF[cas9DF["annoCas12"]==True]

Empty DataFrame
Columns: [HasCRISPR?, annoCRISPR?, Cas1, Cas2, Cas9, Cas12, annoCas1, annoCas2, annoCas9, annoCas12, Cas9 Name]
Index: []

In [8]:
c=0
for accession in masterDF[masterDF["HasCRISPR?"]==False].index:
    if accession in crisprs:
        masterDF.at[accession,"HasCRISPR?"] = True
        c+=1
c     

18955

# Stats on what was found

In [112]:
print("Gene\tMine\tRefSeq\tBoth\tMissed\tPerc")
for gene in ["Cas2","Cas9","Cas12"]:
    print(gene,len(masterDF[masterDF[gene]==True]),len(masterDF[masterDF["anno"+gene]==True]),
          len(masterDF[((masterDF[gene]==True) & (masterDF["anno"+gene]==True))]),
          len(masterDF[((masterDF[gene]==False) & (masterDF["anno"+gene]==True))]),
          len(masterDF[((masterDF[gene]==True) & (masterDF["anno"+gene]==True))]) / float(len(masterDF[masterDF["anno"+gene]==True]))*100,sep='\t')

Gene	Mine	RefSeq	Both	Missed	Perc
Cas2	13203	64533	9351	55182	14.490260796801635
Cas9	28007	13321	11449	1872	85.94700097590271


ZeroDivisionError: float division by zero

<table align="left">
    <tr>
        <th>Component</th>
        <th>Pipeline</th>
        <th>RefSeq</th>
        <th>Both</th>
        <th>Perc</th>
    </tr>
    <tr>
        <td>CRISPR</td>
        <td>1</td>
        <td>0.1617</td>
        <td>0.161704</td>
        <td>3.0101</td>
    </tr>
    <tr>
        <td>Cas1</td>
        <td>134</td>
        <td>7.1986</td>
        <td>0.053721</td>
        <td></td>
    </tr>
    <tr>
        <td>Cas2</td>
        <td>135</td>
        <td>7.3603</td>
        <td></td>
        <td></td>
    </tr>
    <tr>
        <td>Cas9</td>
        <td>135</td>
        <td>7.3603</td>
        <td></td>
        <td></td>
    </tr>
    <tr>
        <td>Cas12</td>
        <td>135</td>
        <td>7.3603</td>
        <td></td>
        <td></td>
    </tr>
</table>

In [106]:
masterDF.head()

HasCRISPR?  annoCRISPR?   Cas1   Cas2   Cas9  Cas12  annoCas1  \
GCF_003394085.1      False        False  False  False  False  False     False   
GCF_000740335.1      False        False  False  False  False  False     False   
GCF_006441575.1      False        False  False  False  False  False     False   
GCF_001978415.1      False        False  False  False  False  False     False   
GCF_001588735.1       True         True  False  False   True  False     False   

                 annoCas2  annoCas9  annoCas12  
GCF_003394085.1     False     False      False  
GCF_000740335.1     False     False      False  
GCF_006441575.1     False     False      False  
GCF_001978415.1     False     False      False  
GCF_001588735.1     False     False      False

In [74]:
cas1=read_csv("tables/CasProteins_cas1.csv")
cas1.set_index("Accession",inplace=True)
print(len(cas1[cas1["Cas1"]==True]))
cas1.head()

174352


Cas1
Accession             
GCF_002880835.1   True
GCF_003009065.1   True
GCF_000554285.1  False
GCF_000411875.1   True
GCF_005039855.1   True

In [11]:
crSystems = masterDF[masterDF["HasCRISPR?"]==True]
print(len(crSystems))
hasA_Protein = crSystems[((crSystems["Cas1"]==True)|(crSystems["Cas2"]==True)|(crSystems["Cas9"]==True)|\
                          (crSystems["Cas12"]==True)|(crSystems["annoCas1"]==True)|(crSystems["annoCas2"]==True)\
                         |(crSystems["annoCas9"]==True)|(crSystems["annoCas12"]==True))]
len(hasA_Protein)

157821


94566

In [12]:
from os import system
refseqPath= "/mnt/research/germs/shane/databases/assemblies/NCBI/refseq/bacteria/%s.fasta"

for accession in hasA_Protein.index:
    system("ln -s %s assemblies/crisprAnnotated/" %(refseqPath%accession))

In [13]:
done